In [74]:

import torch
import torch.nn.functional as F
from torch import nn
from torch.autograd import Variable
import torchvision.transforms as transforms
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score
import numpy as np
import pandas as pd



class LogisticRegressionModel(nn.Module):
    def __init__(self, input_dim, output_dim):
        super(LogisticRegressionModel, self).__init__()
        self.linear = nn.Linear(input_dim, output_dim)
        self.sigmoid = nn.Sigmoid()
    def forward(self, x):
        out = self.linear(x)
        return self.sigmoid(out)

np.set_printoptions(suppress=False)
data_train = pd.read_csv("data_train.csv")
data_test = pd.read_csv("data_test.csv")
data_val = pd.read_csv("data_val.csv")
FEATURES =  [ 'age','hypertension','heart_disease','ever_married', 'avg_glucose_level', 'bmi']


In [75]:
x_train = data_train[FEATURES].astype(np.float32)
y_train = data_train['stroke'].astype(np.float32)

x_test = data_test[FEATURES].astype(np.float32)
y_test = data_test['stroke'].astype(np.float32)



fTrain = torch.from_numpy(x_train.values)
tTrain = torch.from_numpy(y_train.values.reshape(2945,1))

fTest= torch.from_numpy(x_test.values)
tTest = torch.from_numpy(y_test.values)


In [76]:

batch_size = 150
n_iters = 1000
num_epochs = 10

In [77]:
input_dim = 6
output_dim = 1

model = LogisticRegressionModel(input_dim, output_dim)


In [78]:
learning_rate = 0.001

criterion = torch.nn.BCELoss(reduction='mean') 
optimizer = torch.optim.SGD(model.parameters(), lr = learning_rate)

In [79]:
print(list(model.parameters())[0].size())
print(list(model.parameters())[1].size())

torch.Size([1, 6])
torch.Size([1])


In [80]:
for epoch in range(num_epochs):
    print ("Epoch #",epoch)
    model.train()
    optimizer.zero_grad()
    # Forward pass
    y_pred = model(fTrain)
    # Compute Loss
    loss = criterion(y_pred, tTrain)
    print(loss.item())
    # Backward pass
    loss.backward()
    optimizer.step()

Epoch # 0
0.34391772747039795
Epoch # 1
0.3400452435016632
Epoch # 2
0.33628249168395996
Epoch # 3
0.3326331079006195
Epoch # 4
0.3291005790233612
Epoch # 5
0.32568827271461487
Epoch # 6
0.32239940762519836
Epoch # 7
0.3192369043827057
Epoch # 8
0.3162035048007965
Epoch # 9
0.31330153346061707


In [81]:

y_pred = model(fTest)
print("predicted Y value: ", y_pred.data)

predicted Y value:  tensor([[0.0089],
        [0.0051],
        [0.1535],
        [0.1008],
        [0.0365],
        [0.0014],
        [0.1275],
        [0.0172],
        [0.1439],
        [0.0088],
        [0.0013],
        [0.3466],
        [0.0078],
        [0.0303],
        [0.0024],
        [0.0607],
        [0.0556],
        [0.0826],
        [0.0765],
        [0.0027],
        [0.0869],
        [0.0424],
        [0.0013],
        [0.1338],
        [0.0017],
        [0.0020],
        [0.0009],
        [0.0014],
        [0.0090],
        [0.4073],
        [0.0026],
        [0.0009],
        [0.0141],
        [0.0897],
        [0.3593],
        [0.3849],
        [0.0073],
        [0.0204],
        [0.1406],
        [0.0053],
        [0.3840],
        [0.0802],
        [0.0068],
        [0.0190],
        [0.3849],
        [0.0034],
        [0.0045],
        [0.3272],
        [0.0397],
        [0.3087],
        [0.0162],
        [0.0159],
        [0.0033],
        [0.0559],
        

In [87]:
print ("The accuracy is", accuracy_score(tTest, np.argmax(y_pred.detach().numpy(), axis=1)))

The accuracy is 0.9480651731160896


In [83]:
torch.save(model, 'stroke.pkl')